# Riemann scheme. 

Lets consider same setup as in [ex_3a](https://github.com/AST-Course/AST5110/blob/main/ex_3a.ipynb) Burgers’ equation, i.e.,

$$\frac{\partial u}{\partial t} + u \frac{\partial u}{\partial x} = 0   \tag{1}$$ 

for the domain $x \in (x_0, x_f)$ with $x_0 = −1.4$, $x_f = 2.0$ with initial condition:

$$u(x,t=0) = A\left[\tanh\left(\frac{x+x_c}{W}\right)-\tanh\left(\frac{x-x_c}{W}\right)\right]   \tag{2}$$

whereby $A = 0.02$ , $x_c = 0.70$, $W = 0.1$. Let the solution evolve until time $t_f = 100$. However, let's now implement a new time-step method. Find the conservative form of the equation and implement a Rieman solver [wiki:Rieman Solvers](https://github.com/AST-Course/AST5110/wiki/Riemann-solvers). 

Add this to your library and solve the previous simulation imposing the CFL condition. For this exercise, fill in `nm_lib` the function `evolv_Rie_uadv_burgers`. 

**Explain why the flux becomes $u^2 /2$**

In [1]:
import numpy as np 
import matplotlib.pyplot as plt 
from nm_lib import nm_lib as nm
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

In [2]:
def initial_u(xx):
    A = 0.02
    x_c = 0.7
    W = 0.1

    return A*(np.tanh((x+x_c)/W) - np.tanh((x-x_c)/W))

In [3]:
nint = 128
nump = nint +1 

x0 = -1.4
xf = 2.0

nt = 100

x = np.linspace(x0,xf, nump)
print(x[1] - x[0])

u0 = initial_u(x)

0.026562500000000044


In [4]:
# u_L = u0[:-1]
# u_R = u0[1:]
# # [abs,abs]
# a = np.max(np.abs(u_L), np.abs(u_R))
# print(a)

#### 1 step

Compute left and right of $u$, i.e., $u_L$ and $u_R$

#### 2 step
Compute from those the flux, i.e., $F_L$ and $F_R$

#### 3 step
Compute the propagating speed ($v_a[i]=max(|u[i],|u[i-1]|)$)

#### 4 step
Compute the interface fluxes (Rusanov)

$rhs=(F_R+F_L)/2 - v_a (U_R -U_L)$

#### 5 step
Advance in time $u^{n+1}=u^n + dt\times rhs$. What is dt? 


In [5]:
# u_L = u0[:-1]
# u_R = u0[1:]
# # [abs,abs]
# a = np.max(np.abs(u_L), np.abs(u_R))
# print(a)


In [6]:
def evolv_Rie_uadv_burgers(xx, uu, numps, nt, bnd_type='wrap', bnd_limits=[1,0], **kwargs):

    #Step 1:
    # u_L = uu[:-1]
    # u_R = uu[1:]

    # print(u_L)

    #Step 2:
    # F_L = (u_L**2)/2
    # F_R = (u_R**2)/2

    #Step 3: 

    # va = np.zeros(numps-1)
    # for i in range(len(va)): 
    #     va[i] = np.max(np.array([np.abs(u_R[i]), np.abs(u_L[i])]))
    
    # rhs = (F_R + F_L)/2 - va*(u_R - u_L)
    
    dx = xx[1] - xx[0]
    # dt = np.min(dx/np.abs(va))

    t = np.zeros(nt)
    un = np.zeros((len(xx), nt))

    un[:,0] = uu
    d = len(un)

    for i in range(nt-1):

        u_L = un[:-1,i]
        u_R = un[1:,i]

        F_L = (u_L**2)/2
        F_R = -(u_R**2)/2

        va = np.zeros(numps-1)
        for j in range(len(va)): 
            va[j] = np.max(np.array([np.abs(u_R[j]), np.abs(u_L[j])]))

        dt = 0.98*np.min(dx/np.abs(va)) 
        rhs = ((F_R + F_L)/2 - va*(u_R - u_L))

        un[1:,i+1] = un[1:,i] + rhs*dt
        t[i+1] = t[i]+dt
        un[:,i+1] = np.pad(un[bnd_limits[0]:d- bnd_limits[1],i+1], bnd_limits, bnd_type)
        u = un[:,i+1]

    return t, un

nt = 1000
t, un = evolv_Rie_uadv_burgers(x, u0, nump, nt, bnd_limits=[1,0])

t_lax, un_lax = nm.evolv_Lax_uadv_burgers(x, u0, nt, ddx = nm.deriv_cent, bnd_limits=[1,0])



In [7]:
same = t_lax.reshape(len(t_lax),1) - t
same2 = np.where(np.abs(same)<0.5)

In [8]:
plt.ioff()

fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 5))

def init(): 
    axes.plot(x,un[:,0])

def animate(i):
 
    axes.clear()
    axes.plot(x,un[:,::10][:,i])
    axes.set_title('t=%.2f'%t[::10][i])
    axes.grid()
    
anim = FuncAnimation(fig, animate, interval=50, frames=len(t[::10]), init_func=init)
HTML(anim.to_jshtml())



# fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 5))

# def init(): 
#     axes.plot(x,un[:,0])

# def animate(i):
 
#     axes.clear()
#     axes.plot(x,un[:,i])
#     axes.set_title('t=%.2f'%t[i])
#     axes.grid()
    
# anim = FuncAnimation(fig, animate, interval=50, frames=nt, init_func=init)
# HTML(anim.to_jshtml())

In [9]:
plt.close()

In [10]:
plt.ioff()

fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 5))

def init(): 
    axes.plot(x,un[:,0])
    axes.plot(x,un_lax[:,0])

def animate(i):
 
    axes.clear()
    axes.plot(x,un[:,same2[1]][:,::10][:,i], label="Riemann")
    axes.plot(x,un_lax[:,same2[0]][:,::10][:,i], label="LAX")
    axes.set_title('t=%.2f'%t[same2[1]][::10][i])
    axes.legend()
    
anim = FuncAnimation(fig, animate, interval=50, frames=len(t[same2[1]][::10]), init_func=init)
HTML(anim.to_jshtml())

In [11]:
plt.close()

Is this method less or more diffusive than Lax method? Find the analytical solution and compare. Where and when is better or worse than the Lax method? 

---
## TVD scheme. 

Combine the Lax method with the Rieman solver using a flux limiter scheme. For this, one needs to identify how large are the gradients. Lets define: 

$$r^{+}_i = \frac{u_i-u_{i-1}}{u_{i+1}+u_i}$$

What kind of properties do you see on $r^{+}_i$? e.g., what happens when $r\ge0$? or $r\le0$? 

now lets consider the following flux limiter: 

$$\phi = max\left(0,min\left(\theta r,\frac{1+r}{2},\theta \right)\right),\, \theta =[1,2]$$

Finally, combine the Lax from previous excersice with the Riemann solver using the flux limiter as follows: 

$$u^{n+1}_i = u^n_i + dt (f^n_{i+1/2}-f^n_{i-1/2})$$

Where 

$$f^n_{i+1/2} = f^{Riemann}_{i+1/2} + \phi^n_i (f^{L}_{i+1/2}-f^{Riemann}_{i+1/2})$$



When becomes purely Rieman solver? And Lax? Which others methods you can find depending on what is $r$ of $\phi$. 